In [1]:
pip install faiss-cpu

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
pip install scikit-image

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [3]:
pip install pinecone-client

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [4]:
pip install datasets

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [5]:
import os
import faiss
import torch
import skimage
import requests
import pinecone
import numpy as np
import pandas as pd
from PIL import Image
from io import BytesIO
import IPython.display
import matplotlib.pyplot as plt
from datasets import load_dataset
from collections import OrderedDict
from transformers import CLIPProcessor, CLIPModel, CLIPTokenizer

In [6]:
def get_model_info(model_ID, device):
# Save the model to device
	model = CLIPModel.from_pretrained(model_ID).to(device)
 	# Get the processor
	processor = CLIPProcessor.from_pretrained(model_ID)
# Get the tokenizer
	tokenizer = CLIPTokenizer.from_pretrained(model_ID)
       # Return model, processor & tokenizer
	return model, processor, tokenizer
# Set the device
device = "cuda" if torch.cuda.is_available() else "cpu"
# Define the model ID
model_ID = "openai/clip-vit-base-patch32"
# Get model, processor & tokenizer
model, processor, tokenizer = get_model_info(model_ID, device)

In [7]:
def get_single_text_embedding(text): 
  inputs = tokenizer(text, return_tensors = "pt")
  text_embeddings = model.get_text_features(**inputs)
  # convert the embeddings to numpy array
  embedding_as_np = text_embeddings.cpu().detach().numpy()
  return embedding_as_np

In [8]:
def get_single_image_embedding(my_image):
  image = processor(
		text = None,
		images = my_image,
		return_tensors="pt"
		)["pixel_values"].to(device)
  embedding = model.get_image_features(image)
  # convert the embeddings to numpy array
  embedding_as_np = embedding.cpu().detach().numpy()
  return embedding_as_np

In [43]:
df = pd.DataFrame(columns=["Prompt Text", "Image File Name", "CLIP Text-Image Cosine Similarity", "CLIP Text-Image-Desc Cosine Similarity","Clip Caption-Prompt-Image Cosine Similarity"])

In [44]:
df

Empty DataFrame
Columns: [Prompt Text, Image File Name, CLIP Text-Image Cosine Similarity, CLIP Text-Image-Desc Cosine Similarity, Clip Caption-Prompt-Image Cosine Similarity]
Index: []

In [32]:
prompt_df = pd.read_csv("C:\\Users\\princ\\Downloads\\Image Dataset\\Image Classes\\InstructPix2Pix_Results_250Calls\\AllPromptsIndividuallyPlacedCSV.csv")

In [12]:
prompt_df

Prompt Number  \
0    Class01_Img01_Prompt01   
1    Class01_Img01_Prompt02   
2    Class01_Img01_Prompt03   
3    Class01_Img01_Prompt04   
4    Class01_Img01_Prompt05   
..                      ...   
245  Class10_Img05_Prompt01   
246  Class10_Img05_Prompt02   
247  Class10_Img05_Prompt03   
248  Class10_Img05_Prompt04   
249  Class10_Img05_Prompt05   

                                                Prompt  \
0                                       Add spectacles   
1                                       Add an earring   
2                   Change the hairstyle to a top-knot   
3             Change the hair color to chocolate brown   
4                      Increase the length of the hair   
..                                                 ...   
245                             Change the tea to beer   
246                      Give glass cup a pinkish tint   
247  Add another similar cup at the back of the one...   
248  Change the tea to a chocolate milk shake with ...   
249  Change the style of the picture into a DeviantArt   

                                BLIP Image Description  \
0            a woman with a black dress and a necklace   
1            a woman with a black dress and a necklace   
2            a woman with a black dress and a necklace   
3            a woman with a black dress and a necklace   
4            a woman with a black dress and a necklace   
..                                                 ...   
245  a glass of coffee with a straw sticking out of it   
246  a glass of coffee with a straw sticking out of it   
247  a glass of coffee with a straw sticking out of it   
248  a glass of coffee with a straw sticking out of it   
249  a glass of coffee with a straw sticking out of it   

                               Final Image Description  \
0            a woman with a black dress and a necklace   
1            a woman with a black dress and a necklace   
2            a woman with a black dress and a necklace   
3            a woman with a black dress and a necklace   
4            a woman with a black dress and a necklace   
..                                                 ...   
245  a glass of coffee with a straw sticking out of it   
246  a glass of coffee with a straw sticking out of it   
247  a glass of coffee with a straw sticking out of it   
248  a glass of coffee with a straw sticking out of it   
249  a glass of coffee with a straw sticking out of it   

                         Chatgpt Combined Descriptions  
0    A woman with a black dress and a necklace, wea...  
1    A woman with a black dress and a necklace, wea...  
2    A woman with a black dress and a necklace, hai...  
3    A woman with a black dress and a necklace, hai...  
4    A woman with a black dress and a necklace, wit...  
..                                                 ...  
245            Change the coffee in the glass to beer.  
246  Give the glass cup containing coffee a pinkish...  
247  Add another similar cup behind the one in the ...  
248  Change the coffee in the glass to a chocolate ...  
249  Change the style of the picture of the glass o...  

[250 rows x 5 columns]

In [42]:
#prompt_df = prompt_df.iloc[0:125]

In [13]:
prompt_df.shape

(250, 5)

In [14]:
prompt_df.shape[0]

250

In [15]:
from sklearn.metrics.pairwise import cosine_similarity

In [15]:
prompt_df.shape[0]

250

In [16]:
for prompt_ind in range(prompt_df.shape[0]):
    prompt_num = prompt_df.iloc[prompt_ind]['Prompt Number']
    prompt_text = prompt_df.iloc[prompt_ind]['Prompt']
    prompt_img_desc = prompt_df.iloc[prompt_ind]['Final Image Description']
    prompt_img_desc = prompt_img_desc + ". " + prompt_text
    print(f"{prompt_text} {prompt_img_desc}")

    inputs = tokenizer(prompt_text, return_tensors = "pt")
    text_embeddings = model.get_text_features(**inputs)
    text_embeddings_as_np = text_embeddings.cpu().detach().numpy()

    prompt_img_desc_inputs = tokenizer(prompt_img_desc, return_tensors="pt")
    prompt_img_desc_text_embeddings = model.get_text_features(**prompt_img_desc_inputs)
    prompt_img_desc_text_embeddings_as_np = prompt_img_desc_text_embeddings.cpu().detach().numpy()
    
    for output_file in os.listdir(r"C:\Users\princ\Downloads\Image Dataset\Image Classes\Plug and Play\PlugAndPlayOutputs"):
        output_filename = output_file[:-4]
        if output_filename == prompt_num:
            output_filepath = r"C:\Users\princ\Downloads\Image Dataset\Image Classes\Plug and Play\PlugAndPlayOutputs\\" + output_file
            output_image = Image.open(output_filepath)
            image = processor(
            text = None,
            images = output_image,
            return_tensors="pt"
            )["pixel_values"]
            image_embedding = model.get_image_features(image)
            image_embedding_as_np = image_embedding.cpu().detach().numpy()
            #print("Image Embeddings")
            #print(image_embedding_as_np)
            cos_sim = cosine_similarity(image_embedding_as_np, text_embeddings_as_np)
            cos_sim = 100*float(cos_sim)
            cos_sim_img_desc = cosine_similarity(image_embedding_as_np, prompt_img_desc_text_embeddings_as_np)
            cos_sim_img_desc = 100*float(cos_sim_img_desc)
            new_row = {"Prompt Text":prompt_text, "Image File Name":output_filename, 
                       "CLIP Text-Image Cosine Similarity":cos_sim, 
                       "CLIP Text-Image-Desc Cosine Similarity":cos_sim_img_desc}
            new_df = pd.DataFrame([new_row])
            df = pd.concat([df, new_df], ignore_index=True)


Add spectacles a woman with a black dress and a necklace. Add spectacles


C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:31: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:33: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:38: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before th

Add an earring a woman with a black dress and a necklace. Add an earring


C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:31: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:33: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)


Change the hairstyle to a top-knot a woman with a black dress and a necklace. Change the hairstyle to a top-knot


...

C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:31: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:33: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)


Add another similar cup at the back of the one in the image. The cup should have a blue straw a glass of coffee with a straw sticking out of it. Add another similar cup at the back of the one in the image. The cup should have a blue straw


C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:31: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:33: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)


Change the tea to a chocolate milk shake with almonds floating a glass of coffee with a straw sticking out of it. Change the tea to a chocolate milk shake with almonds floating
Change the style of the picture into a DeviantArt a glass of coffee with a straw sticking out of it. Change the style of the picture into a DeviantArt


C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:31: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:33: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\3867423722.py:31: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData

In [17]:
df

Prompt Text  \
0                                       Add spectacles   
1                                       Add an earring   
2                   Change the hairstyle to a top-knot   
3             Change the hair color to chocolate brown   
4                      Increase the length of the hair   
..                                                 ...   
245                             Change the tea to beer   
246                      Give glass cup a pinkish tint   
247  Add another similar cup at the back of the one...   
248  Change the tea to a chocolate milk shake with ...   
249  Change the style of the picture into a DeviantArt   

            Image File Name  CLIP Text-Image Cosine Similarity  \
0    Class01_Img01_Prompt01                          27.820617   
1    Class01_Img01_Prompt02                          27.693018   
2    Class01_Img01_Prompt03                          26.755092   
3    Class01_Img01_Prompt04                          28.568751   
4    Class01_Img01_Prompt05                          24.780807   
..                      ...                                ...   
245  Class10_Img05_Prompt01                          27.495626   
246  Class10_Img05_Prompt02                          30.574757   
247  Class10_Img05_Prompt03                          28.262556   
248  Class10_Img05_Prompt04                          28.396732   
249  Class10_Img05_Prompt05                          23.534958   

     CLIP Text-Image-Desc Cosine Similarity  \
0                                 26.775637   
1                                 27.023384   
2                                 27.546477   
3                                 27.957779   
4                                 23.061562   
..                                      ...   
245                               27.256370   
246                               27.712029   
247                               30.927199   
248                               28.453910   
249                               31.429213   

    Clip Caption-Prompt-Image Cosine Similarity  
0                                           NaN  
1                                           NaN  
2                                           NaN  
3                                           NaN  
4                                           NaN  
..                                          ...  
245                                         NaN  
246                                         NaN  
247                                         NaN  
248                                         NaN  
249                                         NaN  

[250 rows x 5 columns]

In [11]:
print("Hello")

Hello


In [20]:
prompt_df.iloc[prompt_ind]['Final Image Description']

'a man in a suit and tie smiling'

In [24]:
prompt_df.iloc[0]['Gemini Combined Descriptions'] = 'A woman with a black dress, a necklace, and spectacles'
prompt_df.iloc[1]['Gemini Combined Descriptions'] = 'A woman with a black dress, a necklace, and an earring adorning one ear.'
prompt_df.iloc[2]['Gemini Combined Descriptions'] = 'A woman with a black dress, a necklace, and her hair styled in a high top-knot.'
prompt_df.iloc[3]['Gemini Combined Descriptions'] = 'A woman with a black dress, a necklace, and her hair colored chocolate brown.'
prompt_df.iloc[4]['Gemini Combined Descriptions'] = 'A woman with a black dress, a necklace, and long hair.'
prompt_df.iloc[5]['Gemini Combined Descriptions'] = 'A man in a suit and tie, sitting in a chair, with his spectacles perched on his nose.'
prompt_df.iloc[6]['Gemini Combined Descriptions'] = 'A man in a suit and tie, sitting in a chair, with a single earring glinting in his ear.'
prompt_df.iloc[7]['Gemini Combined Descriptions'] = 'A man in a suit and tie, sitting in a chair, with his hair styled in a sharp top-knot.'
prompt_df.iloc[8]['Gemini Combined Descriptions'] = 'A man in a suit and tie, sitting in a chair, rich chocolate brown colored hair.'
prompt_df.iloc[9]['Gemini Combined Descriptions'] = 'A man in a suit and tie, sitting in a chair, with long hair'

C:\Users\princ\AppData\Local\Temp\ipykernel_23992\3796482546.py:1: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  prompt_df.iloc[0]['Gemini Combined Descriptions'] = 'A woman with a black dress, a necklace, and spectacles'
C:\Users\princ\AppD

In [28]:
type(prompt_df.iloc[9]['Final Image Description'] )

str

In [29]:
type(prompt_df.iloc[9]['Gemini Combined Descriptions'])

str

In [49]:
for prompt_ind in range(prompt_df.shape[0]):
    prompt_num = prompt_df.iloc[prompt_ind]['Prompt Number']
    prompt_text = prompt_df.iloc[prompt_ind]['Prompt']
    prompt_img_desc = prompt_df.iloc[prompt_ind]['Final Image Description']
    prompt_img_desc = prompt_img_desc + ". " + prompt_text
    print(f"{prompt_text} {prompt_img_desc}")
    prompt_img_comb_desc = prompt_df.iloc[prompt_ind]['Chatgpt Combined Descriptions']

    inputs = tokenizer(prompt_text, return_tensors = "pt")
    text_embeddings = model.get_text_features(**inputs)
    text_embeddings_as_np = text_embeddings.cpu().detach().numpy()

    prompt_img_desc_inputs = tokenizer(prompt_img_desc, return_tensors="pt")
    prompt_img_desc_text_embeddings = model.get_text_features(**prompt_img_desc_inputs)
    prompt_img_desc_text_embeddings_as_np = prompt_img_desc_text_embeddings.cpu().detach().numpy()

    prompt_img_comb_desc_inputs = tokenizer(prompt_img_comb_desc, return_tensors="pt")
    prompt_img_comb_desc_text_embeddings = model.get_text_features(**prompt_img_comb_desc_inputs)
    prompt_img_comb_desc_text_embeddings_as_np = prompt_img_comb_desc_text_embeddings.cpu().detach().numpy()
    
    for output_file in os.listdir(r"C:\Users\princ\Downloads\Image Dataset\Image Classes\ControlNet\ControlNet Output\ControlNet Output"):
        output_filename = output_file[:-4]
        print(output_filename)
        output_filename = output_filename[:7] + "_" + output_filename[7:12] + "_" + output_filename[-8:]
        print(prompt_num)
        if output_filename == prompt_num:
            output_filepath = r"C:\Users\princ\Downloads\Image Dataset\Image Classes\ControlNet\ControlNet Output\ControlNet Output\\" + output_file
            print(output_filename)
            output_image = Image.open(output_filepath)
            image = processor(
            text = None,
            images = output_image,
            return_tensors="pt"
            )["pixel_values"]
            image_embedding = model.get_image_features(image)
            image_embedding_as_np = image_embedding.cpu().detach().numpy()
            #print("Image Embeddings")
            #print(image_embedding_as_np)
            cos_sim = cosine_similarity(image_embedding_as_np, text_embeddings_as_np)
            cos_sim = 100*float(cos_sim)
            cos_sim_img_desc = cosine_similarity(image_embedding_as_np, prompt_img_desc_text_embeddings_as_np)
            cos_sim_img_desc = 100*float(cos_sim_img_desc)
            cos_sim_comb_img_desc = cosine_similarity(image_embedding_as_np, prompt_img_comb_desc_text_embeddings_as_np)
            cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_desc)
            print(f"{cos_sim} {cos_sim_img_desc} {cos_sim_comb_img_desc}")
            new_row = {"Prompt Text":prompt_text, "Image File Name":output_filename, 
                    "CLIP Text-Image Cosine Similarity":cos_sim, 
                    "Clip Caption-Prompt-Image Cosine Similarity":cos_sim_img_desc,
                    "CLIP Combined-TextImage-Desc Cosine Similarity":cos_sim_comb_img_desc}
            new_df = pd.DataFrame([new_row])
            df = pd.concat([df, new_df], ignore_index=True)

Add spectacles a woman with a black dress and a necklace. Add spectacles
Class01Img01Prompt01
Class01_Img01_Prompt01
Class01_Img01_Prompt01


C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:42: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:44: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_

19.915185868740082 19.969138503074646 18.8766211271286
Class01Img01Prompt02
Class01_Img01_Prompt01
Class01Img01Prompt03
Class01_Img01_Prompt01
Class01Img01Prompt04
Class01_Img01_Prompt01
Class01Img01Prompt05
Class01_Img01_Prompt01
Class01Img02Prompt01
Class01_Img01_Prompt01
Class01Img02Prompt02
Class01_Img01_Prompt01
Class01Img02Prompt03
Class01_Img01_Prompt01
Class01Img02Prompt04
Class01_Img01_Prompt01
Class01Img02Prompt05
Class01_Img01_Prompt01
Class01Img03Prompt01
Class01_Img01_Prompt01
Class01Img03Prompt02
Class01_Img01_Prompt01
Class01Img03Prompt03
Class01_Img01_Prompt01
Class01Img03Prompt04
Class01_Img01_Prompt01
Class01Img03Prompt05
Class01_Img01_Prompt01
Class01Img04Prompt01
Class01_Img01_Prompt01
Class01Img04Prompt02
Class01_Img01_Prompt01
Class01Img04Prompt03
Class01_Img01_Prompt01
Class01Img04Prompt04
Class01_Img01_Prompt01
Class01Img04Prompt05
Class01_Img01_Prompt01
Class01Img05Prompt01
Class01_Img01_Prompt01
Class01Img05Prompt02
Class01_Img01_Prompt01
Class01Img05Prompt03


C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:42: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:44: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_

23.74499887228012 21.822133660316467 22.71523028612137
Class01Img01Prompt03
Class01_Img01_Prompt02
Class01Img01Prompt04
Class01_Img01_Prompt02
Class01Img01Prompt05
Class01_Img01_Prompt02
Class01Img02Prompt01
Class01_Img01_Prompt02
Class01Img02Prompt02
Class01_Img01_Prompt02
Class01Img02Prompt03
Class01_Img01_Prompt02
Class01Img02Prompt04
Class01_Img01_Prompt02
Class01Img02Prompt05
Class01_Img01_Prompt02
Class01Img03Prompt01
Class01_Img01_Prompt02
Class01Img03Prompt02
Class01_Img01_Prompt02
Class01Img03Prompt03
Class01_Img01_Prompt02
Class01Img03Prompt04
Class01_Img01_Prompt02
Class01Img03Prompt05
Class01_Img01_Prompt02
Class01Img04Prompt01
Class01_Img01_Prompt02
Class01Img04Prompt02
Class01_Img01_Prompt02
Class01Img04Prompt03
Class01_Img01_Prompt02
Class01Img04Prompt04
Class01_Img01_Prompt02
Class01Img04Prompt05
Class01_Img01_Prompt02
Class01Img05Prompt01
Class01_Img01_Prompt02
Class01Img05Prompt02
Class01_Img01_Prompt02
Class01Img05Prompt03
Class01_Img01_Prompt02
Class01Img05Prompt04


...

C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:42: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:44: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_

29.68444526195526 29.627293348312378 30.14022409915924
Class10Img05Prompt04
Class10_Img05_Prompt03
Class10Img05Prompt05
Class10_Img05_Prompt03
Change the tea to a chocolate milk shake with almonds floating a glass of coffee with a straw sticking out of it. Change the tea to a chocolate milk shake with almonds floating
Class01Img01Prompt01
Class10_Img05_Prompt04
Class01Img01Prompt02
Class10_Img05_Prompt04
Class01Img01Prompt03
Class10_Img05_Prompt04
Class01Img01Prompt04
Class10_Img05_Prompt04
Class01Img01Prompt05
Class10_Img05_Prompt04
Class01Img02Prompt01
Class10_Img05_Prompt04
Class01Img02Prompt02
Class10_Img05_Prompt04
Class01Img02Prompt03
Class10_Img05_Prompt04
Class01Img02Prompt04
Class10_Img05_Prompt04
Class01Img02Prompt05
Class10_Img05_Prompt04
Class01Img03Prompt01
Class10_Img05_Prompt04
Class01Img03Prompt02
Class10_Img05_Prompt04
Class01Img03Prompt03
Class10_Img05_Prompt04
Class01Img03Prompt04
Class10_Img05_Prompt04
Class01Img03Prompt05
Class10_Img05_Prompt04
Class01Img04Prompt01

C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:42: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:44: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_

26.763033866882324 29.489874839782715 30.182871222496033
Class10Img05Prompt05
Class10_Img05_Prompt04
Change the style of the picture into a DeviantArt a glass of coffee with a straw sticking out of it. Change the style of the picture into a DeviantArt
Class01Img01Prompt01
Class10_Img05_Prompt05
Class01Img01Prompt02
Class10_Img05_Prompt05
Class01Img01Prompt03
Class10_Img05_Prompt05
Class01Img01Prompt04
Class10_Img05_Prompt05
Class01Img01Prompt05
Class10_Img05_Prompt05
Class01Img02Prompt01
Class10_Img05_Prompt05
Class01Img02Prompt02
Class10_Img05_Prompt05
Class01Img02Prompt03
Class10_Img05_Prompt05
Class01Img02Prompt04
Class10_Img05_Prompt05
Class01Img02Prompt05
Class10_Img05_Prompt05
Class01Img03Prompt01
Class10_Img05_Prompt05
Class01Img03Prompt02
Class10_Img05_Prompt05
Class01Img03Prompt03
Class10_Img05_Prompt05
Class01Img03Prompt04
Class10_Img05_Prompt05
Class01Img03Prompt05
Class10_Img05_Prompt05
Class01Img04Prompt01
Class10_Img05_Prompt05
Class01Img04Prompt02
Class10_Img05_Prompt05


C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:42: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_20028\4252631480.py:44: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_

In [50]:
df.shape

(250, 6)

In [21]:
df = df.iloc[:-250]

In [51]:
df.head()

Prompt Text         Image File Name  \
0                            Add spectacles  Class01_Img01_Prompt01   
1                            Add an earring  Class01_Img01_Prompt02   
2        Change the hairstyle to a top-knot  Class01_Img01_Prompt03   
3  Change the hair color to chocolate brown  Class01_Img01_Prompt04   
4           Increase the length of the hair  Class01_Img01_Prompt05   

   CLIP Text-Image Cosine Similarity CLIP Text-Image-Desc Cosine Similarity  \
0                          19.915186                                    NaN   
1                          23.744999                                    NaN   
2                          26.202464                                    NaN   
3                          25.856552                                    NaN   
4                          22.147691                                    NaN   

   Clip Caption-Prompt-Image Cosine Similarity  \
0                                    19.969139   
1                                    21.822134   
2                                    27.706507   
3                                    26.738140   
4                                    23.130915   

   CLIP Combined-TextImage-Desc Cosine Similarity  
0                                       18.876621  
1                                       22.715230  
2                                       27.462459  
3                                       29.566371  
4                                       21.677743

In [54]:
df.drop(columns=["CLIP Text-Image-Desc Cosine Similarity"], inplace=True)

KeyError: "['CLIP Text-Image-Desc Cosine Similarity'] not found in axis"

In [55]:
df.to_csv("C:\\Users\\princ\\Downloads\\Image Dataset\\Image Classes\\ControlNet\\Results\\CLIP_Results_General_PromptText_GPT4.csv")

In [26]:
prompt_desc_df = pd.DataFrame(columns=["Prompt Text", "Image Description", "Image File Name", "CLIP Prompt-Image Cosine Similarity", "CLIP Prompt-Desc-Image Cosine Similarity"])

In [ ]:
for prompt_ind in range(prompt_df.shape[0]):
    prompt_num = prompt_desc_df.iloc[prompt_ind]['Prompt Number']
    prompt_text = prompt_desc_df.iloc[prompt_ind]['Prompt']
    prompt_img_desc = prompt_desc_df.iloc[prompt_ind]['Image Description']
    prompt = prompt_img_desc + "." + prompt_text
    # if prompt_num.startswith("Class10"):
    #     print(f"{prompt_num} --> {prompt_text}")
    # print(f"{prompt_num} --> {prompt_text}")
    inputs = tokenizer(prompt, return_tensors = "pt")
    text_embeddings = model.get_text_features(**inputs)
    # convert the embeddings to numpy array
    text_embeddings_as_np = text_embeddings.cpu().detach().numpy()
    #print("Text Embeddings")
    #print(text_embeddings_as_np)

    for output_file in os.listdir(r"C:\Users\princ\Downloads\Image Dataset\Image Classes\InstructPix2Pix_Results_250Calls\All Results Combined For Data Processing"):
        output_filename = output_file[:-4]
        #print(f"{output_filename} and {prompt_num}")
        if output_filename == prompt_num:
            # if prompt_num.startswith("Class10"):
            #     print(f"{prompt_num} --> {prompt_text}")
            output_filepath = r"C:\Users\princ\Downloads\Image Dataset\Image Classes\InstructPix2Pix_Results_250Calls\All Results Combined For Data Processing\\" + output_file
            output_image = Image.open(output_filepath)
            image = processor(
            text = None,
            images = output_image,
            return_tensors="pt"
            )["pixel_values"]
            image_embedding = model.get_image_features(image)
            image_embedding_as_np = image_embedding.cpu().detach().numpy()
            #print("Image Embeddings")
            #print(image_embedding_as_np)
            cos_sim = cosine_similarity(image_embedding_as_np, text_embeddings_as_np)
            cos_sim = 100*float(cos_sim)
            new_row = {"Prompt Text":prompt_text, "Image File Name":output_filename, "CLIP Text-Image Cosine Similarity":cos_sim}
            new_df = pd.DataFrame([new_row])
            df = pd.concat([df, new_df], ignore_index=True)

In [74]:
prompt_text = "actor and daughters uk premiere held"
inputs = tokenizer(prompt_text, return_tensors = "pt")
text_embeddings = model.get_text_features(**inputs)
text_embeddings_as_np = text_embeddings.cpu().detach().numpy()

output_filepath = r"C:\\Users\\princ\\Downloads\\ActorAndDaughtersUKPremiereHeld.jpg"
output_image = Image.open(output_filepath)
image = processor(
text = None,
images = output_image,
return_tensors="pt"
)["pixel_values"]
image_embedding = model.get_image_features(image)
image_embedding_as_np = image_embedding.cpu().detach().numpy()

cos_sim = cosine_similarity(image_embedding_as_np, text_embeddings_as_np)
cos_sim = 100*float(cos_sim)
print(cos_sim)

29.89923059940338


C:\Users\princ\AppData\Local\Temp\ipykernel_12580\4032482355.py:17: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)


In [ ]:
for prompt_ind in range(prompt_df.shape[0]):
    prompt_num = prompt_df.iloc[prompt_ind]['Prompt Number']
    prompt_text = prompt_df.iloc[prompt_ind]['Prompt']
    prompt_img_desc = prompt_df.iloc[prompt_ind]['Final Image Description']
    prompt_img_desc = prompt_img_desc + ". " + prompt_text
    print(f"{prompt_text} {prompt_img_desc}")
    prompt_img_comb_desc = prompt_df.iloc[prompt_ind]['Chatgpt Combined Descriptions']

    inputs = tokenizer(prompt_text, return_tensors = "pt")
    text_embeddings = model.get_text_features(**inputs)
    text_embeddings_as_np = text_embeddings.cpu().detach().numpy()

    prompt_img_desc_inputs = tokenizer(prompt_img_desc, return_tensors="pt")
    prompt_img_desc_text_embeddings = model.get_text_features(**prompt_img_desc_inputs)
    prompt_img_desc_text_embeddings_as_np = prompt_img_desc_text_embeddings.cpu().detach().numpy()

    prompt_img_comb_desc_inputs = tokenizer(prompt_img_comb_desc, return_tensors="pt")
    prompt_img_comb_desc_text_embeddings = model.get_text_features(**prompt_img_comb_desc_inputs)
    prompt_img_comb_desc_text_embeddings_as_np = prompt_img_comb_desc_text_embeddings.cpu().detach().numpy()
    
    for output_file in os.listdir(r"C:\Users\princ\Downloads\Image Dataset\Image Classes\Plug and Play 250 calls\All Results Combined"):
        output_filename = output_file[:-4]
        if output_filename == prompt_num:
            output_filepath = r"C:\Users\princ\Downloads\Image Dataset\Image Classes\Plug and Play 250 calls\All Results Combined\\" + output_file
            output_image = Image.open(output_filepath)
            image = processor(
            text = None,
            images = output_image,
            return_tensors="pt"
            )["pixel_values"]
            image_embedding = model.get_image_features(image)
            image_embedding_as_np = image_embedding.cpu().detach().numpy()
            #print("Image Embeddings")
            #print(image_embedding_as_np)
            cos_sim = cosine_similarity(image_embedding_as_np, text_embeddings_as_np)
            cos_sim = 100*float(cos_sim)
            cos_sim_img_desc = cosine_similarity(image_embedding_as_np, prompt_img_desc_text_embeddings_as_np)
            cos_sim_img_desc = 100*float(cos_sim_img_desc)
            cos_sim_comb_img_desc = cosine_similarity(image_embedding_as_np, prompt_img_comb_desc_text_embeddings_as_np)
            cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_desc)
            print(f"{cos_sim} {cos_sim_img_desc} {cos_sim_comb_img_desc}")
            new_row = {"Prompt Text":prompt_text, "Image File Name":output_filename, 
                    "CLIP Text-Image Cosine Similarity":cos_sim, 
                    "Clip Caption-Prompt-Image Cosine Similarity":cos_sim_img_desc,
                    "CLIP Combined-TextImage-Desc Cosine Similarity":cos_sim_comb_img_desc}
            new_df = pd.DataFrame([new_row])
            df = pd.concat([df, new_df], ignore_index=True)

For Plug and Play Results

In [19]:
df = pd.DataFrame(columns=["Prompt Text", "Image File Name", "CLIP Text-Image Cosine Similarity", "CLIP Text-Image-Desc Cosine Similarity","Clip Caption-Prompt-Image Cosine Similarity"])

In [20]:
for prompt_ind in range(prompt_df.shape[0]):
    prompt_num = prompt_df.iloc[prompt_ind]['Prompt Number']
    prompt_text = prompt_df.iloc[prompt_ind]['Prompt']
    prompt_img_desc = prompt_df.iloc[prompt_ind]['Final Image Description']
    prompt_img_desc = prompt_img_desc + ". " + prompt_text
    print(f"{prompt_text} {prompt_img_desc}")
    prompt_img_comb_desc = prompt_df.iloc[prompt_ind]['Chatgpt Combined Descriptions']

    inputs = tokenizer(prompt_text, return_tensors = "pt")
    text_embeddings = model.get_text_features(**inputs)
    text_embeddings_as_np = text_embeddings.cpu().detach().numpy()

    prompt_img_desc_inputs = tokenizer(prompt_img_desc, return_tensors="pt")
    prompt_img_desc_text_embeddings = model.get_text_features(**prompt_img_desc_inputs)
    prompt_img_desc_text_embeddings_as_np = prompt_img_desc_text_embeddings.cpu().detach().numpy()

    prompt_img_comb_desc_inputs = tokenizer(prompt_img_comb_desc, return_tensors="pt")
    prompt_img_comb_desc_text_embeddings = model.get_text_features(**prompt_img_comb_desc_inputs)
    prompt_img_comb_desc_text_embeddings_as_np = prompt_img_comb_desc_text_embeddings.cpu().detach().numpy()
    
    for output_file in os.listdir(r"C:\Users\princ\Downloads\Image Dataset\Image Classes\Plug and Play 250 calls\All Results Combined"):
        output_filename = output_file[:-4]
        if output_filename == prompt_num:
            output_filepath = r"C:\Users\princ\Downloads\Image Dataset\Image Classes\Plug and Play 250 calls\All Results Combined\\" + output_file
            output_image = Image.open(output_filepath)
            image = processor(
            text = None,
            images = output_image,
            return_tensors="pt"
            )["pixel_values"]
            image_embedding = model.get_image_features(image)
            image_embedding_as_np = image_embedding.cpu().detach().numpy()
            #print("Image Embeddings")
            #print(image_embedding_as_np)
            cos_sim = cosine_similarity(image_embedding_as_np, text_embeddings_as_np)
            cos_sim = 100*float(cos_sim)
            cos_sim_img_desc = cosine_similarity(image_embedding_as_np, prompt_img_desc_text_embeddings_as_np)
            cos_sim_img_desc = 100*float(cos_sim_img_desc)
            cos_sim_comb_img_desc = cosine_similarity(image_embedding_as_np, prompt_img_comb_desc_text_embeddings_as_np)
            cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_desc)
            print(f"{cos_sim} {cos_sim_img_desc} {cos_sim_comb_img_desc}")
            new_row = {"Prompt Text":prompt_text, "Image File Name":output_filename, 
                    "CLIP Text-Image Cosine Similarity":cos_sim, 
                    "Clip Caption-Prompt-Image Cosine Similarity":cos_sim_img_desc,
                    "CLIP Combined-TextImage-Desc Cosine Similarity":cos_sim_comb_img_desc}
            new_df = pd.DataFrame([new_row])
            df = pd.concat([df, new_df], ignore_index=True)

Add spectacles a woman with a black dress and a necklace. Add spectacles


C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:36: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_des

27.820616960525513 26.77563726902008 25.821125507354736
Add an earring a woman with a black dress and a necklace. Add an earring


C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:36: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_des

27.693018317222595 27.02338397502899 25.911399722099304
Change the hairstyle to a top-knot a woman with a black dress and a necklace. Change the hairstyle to a top-knot


...

C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:36: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_des

28.262555599212646 30.927199125289917 30.18220365047455
Change the tea to a chocolate milk shake with almonds floating a glass of coffee with a straw sticking out of it. Change the tea to a chocolate milk shake with almonds floating


C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:36: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_des

28.39673161506653 28.45391035079956 31.030291318893433
Change the style of the picture into a DeviantArt a glass of coffee with a straw sticking out of it. Change the style of the picture into a DeviantArt
23.534958064556122 31.429213285446167 31.991955637931824


C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:36: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim = 100*float(cos_sim)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:38: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_img_desc = 100*float(cos_sim_img_desc)
C:\Users\princ\AppData\Local\Temp\ipykernel_38384\181365934.py:40: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  cos_sim_comb_img_desc = 100*float(cos_sim_comb_img_des

In [22]:
df.drop(columns=["CLIP Text-Image-Desc Cosine Similarity"], inplace=True)

In [24]:
df.to_csv("C:\\Users\\princ\\Downloads\\Image Dataset\\Image Classes\\Plug and Play 250 calls\\CLIP_Results_General_PromptText_GPT4.csv")